### Load libraries and external data

In [1]:
%load_ext autoreload
%autoreload 2

In [2]:
from data import dataloader
import json
from neuralnet import nn
import numpy as np
import pixiedust_node

Pixiedust database opened successfully


#### Load data from Firebase.
Requires [Firebase service account credentials](https://console.firebase.google.com/project/tingle-pilot-collected-data/settings/serviceaccounts/adminsdk) in JSON format saved in `./firebase-credentials`.

In [3]:
pilot_data = dataloader.break_out_blocks(
    dataloader.load_from_firebase()
)

pixiedust_node 0.2.5 started. Cells starting '%%node' may contain Node.js code.
Data loaded from Firebase!


#### Load [Synaptic](http://caza.la/synaptic/)

In [4]:
%%node
var synaptic = require('synaptic');
var Neuron = synaptic.Neuron,
  Layer = synaptic.Layer,
  Network = synaptic.Network,
  Trainer = synaptic.Trainer,
  Architect = synaptic.Architect;

Define Perceptron and associated functions

In [5]:
%%node
/**
 * @constructor {function} Perceptron - Function to create synaptic perceptron
 * @see https://github.com/cazala/synaptic/blob/master/README.md
 * @param input
 * @param hidden
 * @param output
 * @this
 */
function Perceptron(input, hidden, output){
  // create the layers
  var inputLayer = new Layer(input);
  var hiddenLayer = new Layer(hidden);
  var outputLayer = new Layer(output);

  // connect the layers
  inputLayer.project(hiddenLayer);
  hiddenLayer.project(outputLayer);

  // set the layers
  this.set({
    input: inputLayer,
    hidden: [hiddenLayer],
    output: outputLayer
  });
}

// extend the prototype chain
Perceptron.prototype = new Network();
Perceptron.prototype.constructor = Perceptron;


/**
 * @function runPerceptronOnList - Function to run a perceptron on an
 * Array of Numeric input Arrays and return an Array of Numeric output Arrays.
 * @parameter {Perceptron} perceptron
 * @parameter {Numeric[][]} listOfInputs
 * @returns {Numeric[][]}
 */
function runPerceptronOnList(perceptron, listOfInputs){
  var outputs = [];
  for(var i=0; i<listOfInputs.length; i++){
    outputs.push(perceptron.activate(listOfInputs[i]));
  }
  return(outputs);
}

... ... ... ...


---
### See all targets, number of available samples and iteration blocks

In [6]:
for target in list(pilot_data.target.unique()):
    ib =max(
        pilot_data.loc[
            pilot_data.target==target
        ].iteration_block.dropna()
    )
    print(": ".join([
        target,
        "{0} on-target samples in {1} iteration block{2}".format(
            str(len(pilot_data.loc[
                (pilot_data.target == target) &
                (pilot_data.ontarget)
            ])),
            "%.0f" % ib,
            "s" if ib != 1 else ""
        )
    ]))

... ... ... ... ... ... ... ... ... ... ... ... ... ... ... ...
... ... ... ... ... ...
... ... ..... ..... ... ...
none: 19 on-target samples in 2 iteration blocks
environment: 106 on-target samples in 4 iteration blocks
body: 101 on-target samples in 2 iteration blocks
cup: 33 on-target samples in 3 iteration blocks
food: 35 on-target samples in 4 iteration blocks
nails: 69 on-target samples in 3 iteration blocks
smoke: 92 on-target samples in 3 iteration blocks
eyebrow: 235 on-target samples in 5 iteration blocks
nose: 249 on-target samples in 4 iteration blocks
above-ear: 403 on-target samples in 5 iteration blocks
behind-ear: 220 on-target samples in 4 iteration blocks
opposite-cheek: 74 on-target samples in 6 iteration blocks
chin: 166 on-target samples in 1 iteration block
cheek: 686 on-target samples in 6 iteration blocks
forehead: 176 on-target samples in 1 iteration block
top-head: 160 on-target samples in 1 iteration block
back-head: 170 on-target samples in 1 iteration bloc

---
### Extract training and testing data
Define targets of interest and corresponding offtargets

In [7]:
with open(
    'data/targets.json',
    'r'
) as fp:
    targets = json.load(
        fp
    )[0]

Get training inputs and outputs, inputs that should evaluate ~true and inputs that should evaluate ~false

In [29]:
data = {}
for target in targets:
    data[target] = {
        "train": nn.define_trainer_data(
            pilot_data,
            {
                "target": [target],
                "offtarget": targets[target]
            },
            [
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            100,
            scale=98.6
        ),
        "test_true": nn.define_activation(
            pilot_data,
            [target],
            [
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            exclude=100,
            scale=98.6
        ),
        "test_false": nn.define_activation(
            pilot_data,
            targets[target],
            [
                "thermopile1",
                "thermopile2",
                "thermopile3",
                "thermopile4"
            ],
            list(range(1, 7)),
            exclude=100,
            scale=98.6
        )
    }

Preview all inputs and training outputs

In [30]:
data

{'above-ear': {'test_false': [[0.7768762677484787,
    0.8012170385395538,
    0.8002028397565923,
    0.7900608519269778],
   [0.7748478701825559,
    0.8012170385395538,
    0.7860040567951319,
    0.7738336713995944],
   [0.77079107505071, 0.8002028397565923, 0.77079107505071, 0.77079107505071],
   [0.77079107505071,
    0.7890466531440162,
    0.7799188640973632,
    0.7799188640973632],
   [0.7789046653144016,
    0.7961460446247465,
    0.7910750507099392,
    0.7961460446247465],
   [0.7900608519269778,
    0.8022312373225152,
    0.7849898580121705,
    0.7961460446247465],
   [0.7951318458417851,
    0.832657200811359,
    0.8275862068965517,
    0.8225152129817445],
   [0.8002028397565923,
    0.832657200811359,
    0.8397565922920893,
    0.8123732251521298],
   [0.8002028397565923,
    0.8356997971602436,
    0.836713995943205,
    0.8123732251521298],
   [0.8002028397565923,
    0.832657200811359,
    0.8468559837728196,
    0.8204868154158216],
   [0.8002028397565923,
   

**Note**: These data take some time to copy across environments. Give the notebook some time between running cells across Python and JavaScript.

---
### Train and test

In [34]:
%%node
var test_outputs = {};
for(var target in data){
  var perceptron5 = new Perceptron(4,5,5,5,1);
  var perceptron7 = new Perceptron(4,7,7,7,7,7,1);
  var trainer5 = new Trainer(perceptron5);
  var trainer7 = new Trainer(perceptron7);
  test_outputs[target] = {
    "true": {
      "5": [],
      "7": []
    },
    "false": {
      "5": [],
      "7": []
    }
  };
  for(var iteration=0; iteration < data[target]["train"].length; iteration++){
    trainer5.train({
      "input": data[target]["train"][iteration]["input"],
      "output": data[target]["train"][iteration]["output"]
    });
    trainer7.train({
      "input": data[target]["train"][iteration]["input"],
      "output": data[target]["train"][iteration]["output"]
    });
  }
  for(var iteration=0; iteration < data[target]["test_true"].length; iteration++){
    test_outputs[target]["true"]["5"].push(perceptron5.activate(data[target]["test_true"][iteration]));
    test_outputs[target]["true"]["7"].push(perceptron7.activate(data[target]["test_true"][iteration]));
  }
  for(var iteration=0; iteration < data[target]["test_false"].length; iteration++){
    test_outputs[target]["false"]["5"].push(perceptron5.activate(data[target]["test_false"][iteration]));
    test_outputs[target]["false"]["7"].push(perceptron7.activate(data[target]["test_false"][iteration]));
  }
}

... ... ... ... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ..... ..... ... ..... ..... ..... ...
... ... ... ... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ..... ..... ... ..... ..... ..... ...
... ... ... ... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ....... ....... ....... ..... ....... ....... ....... ..... ... ..... ..... ..... ... ..... ..... ..... ...


---
### See outputs

If the training is adequate x ≈ 0 ∀ x in the following:

In [35]:
f = [
    *[
        np.mean(output['5']) for output in [
            outputs['false'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['5'])
    ],
    *[
        np.mean(output['7']) for output in [
            outputs['false'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['7'])
    ]
]
f

[0.5045391101109784,
 0.4914969841944727,
 0.4925630729464032,
 0.5009855998324375,
 0.49672086913407004,
 0.5063573058399242,
 0.5004231280609986,
 0.49209731458763345,
 0.49370969912480966,
 0.4896775289014161,
 0.5133544096515276,
 0.5057710740840287,
 0.5029033561190669,
 0.5138330874721924,
 0.4925303314505327,
 0.5074665738995374,
 0.507863019873093,
 0.4987134889513308,
 0.4958446005190657,
 0.49172285933243615,
 0.4980125474607257,
 0.5054761067516826,
 0.5097679652326195,
 0.48795769358359625,
 0.4994884238745326,
 0.5038124576860712]

If the training is adequate x ≈ 1 ∀ x in the following:

In [36]:
t = [
    *[
        np.mean(output['5']) for output in [
            outputs['true'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['5'])
    ],
    *[
        np.mean(output['7']) for output in [
            outputs['true'] for outputs in [
                test_outputs[i] for i in test_outputs
            ]
        ] if len(output['7'])
    ]
]
t

[0.4925632499584341,
 0.5009849491316173,
 0.4967217270384892,
 0.506343568625385,
 0.4921044725602137,
 0.49371488373505296,
 0.4896770376844401,
 0.5133552277041404,
 0.5057735989010356,
 0.5029003460424246,
 0.5074704746062048,
 0.507868527703543,
 0.4987107280225628,
 0.49585120582352715,
 0.49801783230297236,
 0.5054724008279352,
 0.5097646039989262,
 0.4879739785206901,
 0.49948549726618047,
 0.5037966302072273]

Finally, if training is adequate, f ≪ t:

In [37]:
f_mean = np.mean(f)
t_mean = np.mean(t)
print(
    "f = {0}\nt = {1}\n{0} ≪ {1} ?".format(
        str(f_mean),
        str(t_mean)
    ) if f_mean < t_mean else "Nope. f > t"
)

f = 0.5001187926413533
t = 0.5004275470330501
0.5001187926413533 ≪ 0.5004275470330501 ?
